In [1]:
import sys
sys.path += ['..']

from data_collection.data_collection import LoggerSet, Logger

import numpy as np
import pandas as pd
import plotly.express as px
from data_collection.video_data import get_frame_iterator
from pathlib import Path
from typing import Iterable, Tuple, List
from tqdm import tqdm
import datetime
import tensorflow as tf
import tensorflow.keras as keras

%load_ext autoreload
%autoreload 2


2024-06-11 19:51:06.366752: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-06-11 19:51:07.003361: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


# Note
- Condition: no smoothing and 100ms delay
- still a great fitting

# Loading data 

In [2]:
from with_linear_acc import Session
sessions = Session.load_multiple_session('./data')
frames, df = Session.concatenate_multiple_sessions(sessions)

[mov,mp4,m4a,3gp,3g2,mj2 @ 0x62e650643a00] moov atom not found


## Inspection only

In [3]:
df = sessions[0].data['angular_speed_control_df']

In [4]:

def mean_nominmax(x):
    return (x.sum()-x.max()-x.min())/(len(x)-2)
asd0 = df['angular_velocity'].rolling(100).apply(mean_nominmax).shift(-99)

asd = df['angular_velocity'].rolling(50).apply(mean_nominmax).shift(-49)
asd1 = df['angular_velocity'].rolling(3).apply(mean_nominmax).shift(-2)


px.line(y=[asd1, asd, asd0])

# Select data for the model

In [3]:
def prepare_to_tensorflow(frames, df):

    # data selection
    df = df.query('speed!=0')

    # match the data with the frame
    frame2data = df.groupby('exact_total_frame_idx')[['linacc0', 'linacc1', 'linacc2']].mean()
    outputs = df.groupby('offset_total_frame_idx')[['angular_velocity']].mean()

    # the reindexed data
    frame_indices = outputs.index.values

    frames_reindexed = frames[frame_indices]
    other_inputs = frame2data.reindex(frame_indices)

    # screen out the nans
    nafilter = (~other_inputs.isna().any(axis=1)).values

    frames_reindexed = frames_reindexed[nafilter]
    other_inputs = other_inputs.values[nafilter]
    outputs = outputs.values[nafilter]
    
    
    return frames_reindexed, other_inputs/10, outputs/180

In [4]:
frames_in, other_in, out = prepare_to_tensorflow(frames, df)

In [5]:

from train_tools import validation_chunk_split

In [6]:
train_idx, val_idx = validation_chunk_split(len(frames_in), val_split=0.2)
train_frames, train_other, train_out = frames_in[train_idx], other_in[train_idx], out[train_idx]
val_frames, val_other, val_out = frames_in[val_idx], other_in[val_idx], out[val_idx]

# Model

In [7]:
def get_model(lr=.1, other_metrics=[]):
    tf.keras.backend.clear_session()
    image_shape = 64, 114, 3

    img_aug_preprocess_layers = [
        # keras.layers.RandomTranslation(0.05, 0.05, fill_mode='reflect'),
        # keras.layers.RandomRotation(0.02, fill_mode='reflect'),
        # keras.layers.RandomZoom(0.05, fill_mode='reflect'),
        # keras.layers.RandomContrast(0.5),
        # keras.layers.RandomBrightness([-0.7, 0.7])
    ]
    
    cnn_layers =  [
        keras.layers.Conv2D(16, 5, strides=2, activation='relu'), 
        keras.layers.Conv2D(32, 5, strides=2, activation='relu'), 
        keras.layers.Conv2D(64, 5, strides=2, activation='relu'),         
        keras.layers.Conv2D(64, 3, activation='relu'), 
        keras.layers.Conv2D(96, 3, activation='relu'),         
        keras.layers.Flatten(),
        keras.layers.Dropout(0.2),
    ]
    
    cnn = keras.Sequential(
        [
            keras.layers.InputLayer(image_shape),
            keras.layers.Rescaling(1/255), 
            *img_aug_preprocess_layers,
            *cnn_layers
        ])

    other_inputs = keras.layers.InputLayer((3,))
    x = keras.layers.Concatenate()([cnn.outputs[0], other_inputs.output])
    x = keras.layers.Dense(128, activation='relu')(x)
    x = keras.layers.Dense(64, activation='relu')(x)
    y = keras.layers.Dense(1)(x)

    model = keras.Model([cnn.inputs[0], other_inputs.output], y)


    optimiser = keras.optimizers.Adam(lr)
    model.compile(optimizer=optimiser, loss='Huber', metrics=['MAE']+other_metrics)

    return model 

model = get_model()
model.summary()

2024-06-11 19:51:22.387312: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:998] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
2024-06-11 19:51:22.419161: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:998] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
2024-06-11 19:51:22.419419: I external/local_xla/xla/stream_executor/cuda/cuda_executor.cc:998] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-

Model: "functional_2"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer         │ (None, 64, 114,   │          0 │ -                 │
│ (InputLayer)        │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ rescaling           │ (None, 64, 114,   │          0 │ input_layer[0][0] │
│ (Rescaling)         │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d (Conv2D)     │ (None, 30, 55,    │      1,216 │ rescaling[0][0]   │
│                     │ 16)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_1 (Conv2D)   │ (None, 13, 26,    │     12,832 │ conv2d[0][0]      │
│                     │ 32)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_2 (Conv2D)   │ (None, 5, 11, 64) │     51,264 │ conv2d_1[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_3 (Conv2D)   │ (None, 3, 9, 64)  │     36,928 │ conv2d_2[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2d_4 (Conv2D)   │ (None, 1, 7, 96)  │     55,392 │ conv2d_3[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ flatten (Flatten)   │ (None, 672)       │          0 │ conv2d_4[0][0]    │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dropout (Dropout)   │ (None, 672)       │          0 │ flatten[0][0]     │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ input_layer_1       │ (None, 3)         │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ concatenate         │ (None, 675)       │          0 │ dropout[0][0],    │
│ (Concatenate)       │                   │            │ input_layer_1[0]… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense (Dense)       │ (None, 128)       │     86,528 │ concatenate[0][0] │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_1 (Dense)     │ (None, 64)        │      8,256 │ dense[0][0]       │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_2 (Dense)     │ (None, 1)         │         65 │ dense_1[0][0]     │
└─────────────────────┴───────────────────┴────────────┴───────────────────┘

 Total params: 252,481 (986.25 KB)

 Trainable params: 252,481 (986.25 KB)

 Non-trainable params: 0 (0.00 B)

In [8]:
from train_tools import find_lr, tg_notify, use_tensorboard, end_epoch_notify

In [10]:
find_lr(get_model(), [train_frames, train_other], train_out)
#tensorboard --logdir src/training/logs --bind_all

Epoch 1/100


2024-06-11 19:50:52.107773: W external/local_tsl/tsl/framework/bfc_allocator.cc:487] Allocator (GPU_0_bfc) ran out of memory trying to allocate 200.0KiB (rounded to 204800)requested by op adam/zeros_8
If the cause is memory fragmentation maybe the environment variable 'TF_GPU_ALLOCATOR=cuda_malloc_async' will improve the situation. 
Current allocation summary follows.
Current allocation summary follows.
2024-06-11 19:50:52.107802: I external/local_tsl/tsl/framework/bfc_allocator.cc:1044] BFCAllocator dump for GPU_0_bfc
2024-06-11 19:50:52.107819: I external/local_tsl/tsl/framework/bfc_allocator.cc:1051] Bin (256): 	Total Chunks: 48, Chunks in use: 48. 12.0KiB allocated for chunks. 12.0KiB in use in bin. 3.2KiB client-requested in use in bin.
2024-06-11 19:50:52.107833: I external/local_tsl/tsl/framework/bfc_allocator.cc:1051] Bin (512): 	Total Chunks: 6, Chunks in use: 6. 3.0KiB allocated for chunks. 3.0KiB in use in bin. 2.6KiB client-requested in use in bin.
2024-06-11 19:50:52.10784

RuntimeError: pybind11::error_already_set: MISMATCH of original and normalized active exception types: ORIGINAL ResourceExhaustedError REPLACED BY KeyboardInterrupt: <EMPTY MESSAGE>

At:
  /home/kawa/CurrentProjects/pi_projects/self-driving/remote-control-car-1/venv/lib/python3.10/site-packages/tensorflow/python/framework/errors_impl.py(377): __init__
  /home/kawa/CurrentProjects/pi_projects/self-driving/remote-control-car-1/venv/lib/python3.10/site-packages/tensorflow/python/eager/execute.py(53): quick_execute
  /home/kawa/CurrentProjects/pi_projects/self-driving/remote-control-car-1/venv/lib/python3.10/site-packages/tensorflow/python/eager/context.py(1500): call_function
  /home/kawa/CurrentProjects/pi_projects/self-driving/remote-control-car-1/venv/lib/python3.10/site-packages/tensorflow/python/eager/polymorphic_function/atomic_function.py(251): call_flat
  /home/kawa/CurrentProjects/pi_projects/self-driving/remote-control-car-1/venv/lib/python3.10/site-packages/tensorflow/python/ea

In [9]:
model = get_model(1e-4)
model.fit(
    [train_frames, train_other],
    train_out,
    epochs=100, 
    validation_data = ([val_frames, val_other], val_out),
    callbacks=[
        tf.keras.callbacks.EarlyStopping(monitor='val_loss', patience=10),
        use_tensorboard('training'), 
        end_epoch_notify()
        ] 
    )

Epoch 1/100


I0000 00:00:1718099492.393366  749300 service.cc:145] XLA service 0x7d9ce000ef40 initialized for platform CUDA (this does not guarantee that XLA will be used). Devices:
I0000 00:00:1718099492.393400  749300 service.cc:153]   StreamExecutor device (0): NVIDIA GeForce GTX 1650 SUPER, Compute Capability 7.5
2024-06-11 19:51:32.440002: I tensorflow/compiler/mlir/tensorflow/utils/dump_mlir_util.cc:268] disabling MLIR crash reproducer, set env var `MLIR_CRASH_REPRODUCER_DIRECTORY` to enable.
2024-06-11 19:51:32.674541: I external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:465] Loaded cuDNN version 8907


 47/364 ━━━━━━━━━━━━━━━━━━━━ 1s 3ms/step - MAE: 0.1992 - loss: 0.0461

I0000 00:00:1718099495.785370  749300 device_compiler.h:188] Compiled cluster using XLA!  This line is logged at most once for the lifetime of the process.


364/364 ━━━━━━━━━━━━━━━━━━━━ 9s 13ms/step - MAE: 0.1990 - loss: 0.0466 - val_MAE: 0.2105 - val_loss: 0.0494
Epoch 2/100
364/364 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.2022 - loss: 0.0458 - val_MAE: 0.1887 - val_loss: 0.0420
Epoch 3/100
364/364 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.1971 - loss: 0.0401 - val_MAE: 0.1953 - val_loss: 0.0400
Epoch 4/100
364/364 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.1897 - loss: 0.0350 - val_MAE: 0.1751 - val_loss: 0.0318
Epoch 5/100
364/364 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.1731 - loss: 0.0286 - val_MAE: 0.1597 - val_loss: 0.0286
Epoch 6/100
364/364 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.1628 - loss: 0.0249 - val_MAE: 0.1583 - val_loss: 0.0260
Epoch 7/100
364/364 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.1541 - loss: 0.0224 - val_MAE: 0.1597 - val_loss: 0.0270
Epoch 8/100
364/364 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE: 0.1453 - loss: 0.0202 - val_MAE: 0.1446 - val_loss: 0.0226
Epoch 9/100
364/364 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - MAE:

In [ ]:
#frames_reindexed#, other_inputs_reindexed, outputs

# visualise the performance

In [10]:

#train_frames, train_other, train_out
val_idx = np.sort(val_idx)
train_idx = np.sort(train_idx)

val_y_pred = model.predict([frames_in[val_idx], other_in[val_idx]], batch_size=64)
train_y_pred = model.predict([frames_in[train_idx], other_in[train_idx]], batch_size=64)


val_out = out[val_idx]
train_out = out[train_idx]



33/33 ━━━━━━━━━━━━━━━━━━━━ 1s 7ms/step 
182/182 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step


In [11]:
px.line(np.c_[train_out[:, 0], train_y_pred[:, 0]], title='train')

In [12]:
px.line(np.c_[val_out[:, 0], val_y_pred[:, 0]], title='val')

In [14]:
y_pred = model.predict([val_frames[:], val_other[:]], batch_size=64)

px.line(np.c_[val_out[:, 0], y_pred[:, 0]])

12/12 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step


In [ ]:
#model.save('10Jun-pi.keras')

array([ 112,  113,  114,  115,  116,  117,  118,  119,  120,  121,  122,
        123,  124,  125,  126,  127,  128,  129,  130,  131,  132,  133,
        134,  135,  136,  137,  138,  139,  140,  141,  142,  143,  144,
        145,  146,  147,  148,  149,  150,  151,  152,  153,  154,  155,
        156,  157,  158,  159,  160,  161,  162,  163,  164,  165,  166,
        167,  168,  169,  170,  171,  172,  173,  174,  175,  176,  177,
        178,  179,  180,  181,  182,  183,  184,  185,  186,  187,  188,
        189,  190,  191,  192,  193,  194,  195,  196,  197,  198,  199,
        200,  201,  202,  203,  204,  205,  206,  207,  208,  209,  210,
        211,  212,  213,  214,  215,  216,  217,  218,  219,  220,  221,
        222,  223,  224,  225,  226,  227,  228,  229,  230,  231,  232,
        233,  234,  235,  236,  237,  238,  239,  240,  241,  242,  243,
        244,  245,  246,  247,  248,  249,  250,  251,  252,  253,  254,
        255,  256,  257,  258,  259,  260,  261,  2